In [2]:
import pandas as pd
import numpy as np
from math import sin, cos, sqrt, atan2, radians
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import os
from sklearn import metrics
from sklearn import preprocessing
from sklearn.cluster import KMeans
from sklearn.cluster import DBSCAN
from sklearn.manifold import TSNE
from scipy.spatial.distance import cdist
import plotly.express as px
from plotly.subplots import make_subplots

In [2]:
%%time
df = pd.read_csv('D:\MiniProject_P3_fitrec\endomondo_preprocessed.csv')
print(len(df))

65500
Wall time: 1min 1s


In [3]:
df.head(3)

id    userId gender sport  duration  calories  distance  \
0  396826535  10921915   male  bike      7589    1562.0     53.88   
1  392337038  10921915   male  bike      4440     908.0     32.61   
2  386729739  10921915   male  bike      4519     921.0     32.70   

   avg_heart_rate                                          longitude  \
0          152.65  [24.64977040886879, 24.65014273300767, 24.6509...   
1          147.71  [24.649855233728886, 24.65015547350049, 24.650...   
2          147.02  [24.649874344468117, 24.650242729112506, 24.65...   

                                            latitude  ...  \
0  [60.173348765820265, 60.173239801079035, 60.17...  ...   
1  [60.173247596248984, 60.17320962622762, 60.172...  ...   
2  [60.173286236822605, 60.17323946580291, 60.173...  ...   

                                    derived_distance  \
0  [0.023920359645758085, 0.0513686868631109, 0.0...   
1  [0.01714931222251621, 0.047614484656155226, 0....   
2  [0.02104899112126496, 0.03733382239564792, 0.0...   

                                       derived_speed  \
0  [10.764161840591138, 16.81157024610902, 15.919...   
1  [12.34750480021167, 14.284345396846566, 17.330...   
2  [12.629394672758975, 16.800220078041566, 20.17...   

                                        time_elapsed validate avg_alti  \
0  [8, 11, 13, 16, 6, 23, 16, 23, 29, 23, 24, 24,...     True  43.0712   
1  [5, 12, 8, 4, 5, 6, 4, 4, 5, 13, 7, 17, 4, 10,...     True  35.7248   
2  [6, 8, 9, 4, 13, 4, 3, 4, 13, 10, 13, 13, 7, 1...     True  32.6104   

  change_alti max_alti min_alti  diff_alti  avg_speed  
0       820.6     74.2     14.6       59.6  25.568980  
1       454.2     67.8     17.2       50.6  27.129599  
2       481.4     64.0     12.4       51.6  26.651989  

[3 rows x 25 columns]

Cluster for Running

In [4]:
df_sub = df[df['sport']=='run'].copy()
df_sub.reset_index(drop=1,inplace=True)
df_sub

id   userId gender sport  duration  calories   distance  \
0      321063199  4969375   male   run      3888     436.0   8.650000   
1      303565793  4969375   male   run      4204     577.0  14.370000   
2      296982347  4969375   male   run      6503    1025.0  22.220000   
3      295890426  4969375   male   run      5118     775.0  16.980000   
4      294163731  4969375   male   run      3035     445.0   9.670000   
...          ...      ...    ...   ...       ...       ...        ...   
36896  298971490       69   male   run      2047     623.0   6.013510   
36897  235763396       69   male   run      7387    1374.0  21.310540   
36898  235521923       69   male   run     14106    3000.0  43.460340   
36899  596953078       69   male   run      5122    1554.0  16.069464   
36900   20253456       69   male   run      1789     646.0   5.466285   

       avg_heart_rate                                          longitude  \
0             122.104  [6.8854929, 6.8853678, 6.8851621, 6.8848205, 6...   
1             146.994  [6.9144073, 6.9142929, 6.9141539, 6.9140268, 6...   
2             134.918  [6.8678543, 6.8678634, 6.8675429, 6.8672183, 6...   
3             132.414  [6.9143328, 6.9146396, 6.9148949, 6.9151568, 6...   
4             125.346  [6.9133737, 6.9132722, 6.913217, 6.9131066, 6....   
...               ...                                                ...   
36896         155.294  [11.76463108509779, 11.76454659551382, 11.7644...   
36897         134.108  [11.757076978683472, 11.757056526839733, 11.75...   
36898         147.990  [12.037591952830553, 12.037658086046576, 12.03...   
36899         140.498  [11.76487541, 11.76516151, 11.7653389, 11.7655...   
36900         157.656  [11.7646691, 11.7647482, 11.764898, 11.7650011...   

                                                latitude  ...  \
0      [52.2226809, 52.222727, 52.2228258, 52.2228606...  ...   
1      [52.2111711, 52.2112631, 52.2114064, 52.211608...  ...   
2      [52.1936673, 52.1934354, 52.1931993, 52.192873...  ...   
3      [52.2112195, 52.2110264, 52.2108135, 52.210601...  ...   
4      [52.2111481, 52.2111209, 52.21119, 52.2112981,...  ...   
...                                                  ...  ...   
36896  [55.24085112847388, 55.24080477654934, 55.2407...  ...   
36897  [55.248560551553965, 55.24857848882675, 55.248...  ...   
36898  [55.3915087133646, 55.39149438031018, 55.39146...  ...   
36899  [55.24080276, 55.24095154, 55.24104691, 55.241...  ...   
36900  [55.2406747, 55.2407376, 55.2408083, 55.240875...  ...   

                                        derived_distance  \
0      [0.024692396657788666, 0.02062475820692565, 0....   
1      [0.012866693107454877, 0.018551828170520174, 0...   
2      [0.0258024349522409, 0.034169705873918786, 0.0...   
3      [0.03005678592559137, 0.029397223648873875, 0....   
4      [0.008947091230656174, 0.009208079362029106, 0...   
...                                                  ...   
36896  [0.0074356460011203145, 0.01056021379557203, 0...   
36897  [0.0023795191226302077, 0.03646076766570062, 0...   
36898  [0.0045118658545229, 0.04519099979019238, 0.04...   
36899  [0.02455755616280793, 0.015463299900299304, 0....   
36900  [0.008622179176410893, 0.01234161954467786, 0....   

                                           derived_speed  \
0      [12.698946852577029, 10.911666227748753, 10.05...   
1      [5.790011898354694, 7.923126352508781, 8.85172...   
2      [7.1452896790820954, 9.460093775795364, 10.251...   
3      [10.820442933212894, 10.685701145251175, 10.36...   
4      [5.368254738393704, 6.557825426283524, 7.28499...   
...                                                  ...   
36896  [6.692081401008283, 9.190715975634406, 9.97964...   
36897  [8.566268841468748, 9.99318973861072, 9.922999...   
36898  [2.7071195127137395, 6.44568709366374, 7.45044...   
36899  [8.840720218610855, 9.263224919203076, 9.54057...   
36900  [10.346615011693071, 11.111557448274871, 11.36...   

 

In [5]:
# select faetures
feature = ['id','distance','change_alti','diff_alti','avg_alti','min_alti','max_alti']
df_cluster = df_sub[feature]

train = df_cluster.drop('id',axis=1)
t= preprocessing.StandardScaler().fit(train)
train=t.transform(train)
train

array([[-0.53128381,  1.55083853,  5.31533641, -0.73711031, -1.88479699,
        -0.55548346],
       [ 0.35110375, -0.39426458, -0.28949619, -0.47056389, -0.45780692,
        -0.49740613],
       [ 1.5620727 , -0.24668574, -0.5091739 , -0.49797367, -0.45260436,
        -0.54288837],
       ...,
       [ 4.83868316,  0.47512167, -0.51527606, -0.48659797, -0.43402376,
        -0.52679465],
       [ 0.6132692 , -0.18093972,  0.18342109, -0.4926745 , -0.51949452,
        -0.44702579],
       [-1.02241507,  0.09461253, -0.34804351, -0.56636838, -0.54886929,
        -0.59656617]])

In [6]:
%%time
ch_score = []
ss_score = []
meandistortions = []
# try k from 2 to 15
for k in range(2,15):
    clf = KMeans(n_clusters=k)
    pred = clf.fit_predict(train)
    ch = metrics.calinski_harabasz_score(train,pred)
    ss = metrics.silhouette_score(train,pred)
    ch_score.append(ch)
    ss_score.append(ss)
    meandistortions.append(sum(np.min(cdist(train, clf.cluster_centers_, 'euclidean'), axis=1)) / train.shape[0])

Wall time: 3min 13s


In [7]:
fig = make_subplots(rows=1, cols=3,subplot_titles=("Calinski Harabasz Score", "Elbow Score",'Silhouette Score'))

fig.add_trace(go.Scatter(x=list(range(2,15)), y=ch_score,
                    mode='lines+markers',),row=1,col=1)

fig.add_trace(go.Scatter(x=list(range(2,15)), y=ss_score,
                    mode='lines+markers',
                    name='lines'),row=1,col=3,)

fig.add_trace(go.Scatter(x=list(range(2,15)), y=meandistortions,
                    mode='lines+markers',
                    name='lines'),row=1,col=2,)

fig.update_layout(height=600, width=1200, title_text="Running: Number of K",showlegend=False)
fig.show()

In [8]:
# choose the best number of k
clf = KMeans(n_clusters=6)
pred = clf.fit_predict(train)
pred = [str(i) for i in pred]

In [9]:
# use tsne to plot the clusters
tsne = TSNE(n_components=2, random_state=0)
projections = tsne.fit_transform(train)
projections_df = pd.DataFrame(projections)
projections_df['Cluster']=pred

c:\Users\user\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:780: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

c:\Users\user\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:790: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



In [10]:
fig = px.scatter(
    projections_df, x=0, y=1,
    color='Cluster',
    labels={'color': 'Cluster'},
    category_orders={"Cluster": ["0", "1", "2", "3","4",'5']}
)

fig.update_layout(height=600, width=1200,title='TSNE: Running Route Clustering',font_size=22)
fig.show()

In [11]:
t = df_cluster.copy()
t['K_means'] = pred
t = t.groupby('K_means').mean()

In [12]:
x_axis = ['Cluster '+str(i) for i in range(len(t))]
fig = go.Figure(data=[
    go.Bar(name='Distance', x=x_axis, y=t['distance']*100),
    go.Bar(name='Change of Altitude', x=x_axis, y=t['change_alti']),
    go.Bar(name='Diff_Altitude', x=x_axis, y=t['diff_alti']),
    go.Bar(name='Avg_Altitude', x=x_axis, y=t['avg_alti'])
])
# Change the bar mode
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01))
fig.update_layout(barmode='group',font_size=22,height=600,width=1200,title = 'Clusters of Running')
fig.show()

In [13]:
df_sub['Cluster']=pred
df_run = df_sub.copy()

Cluster for Biking

In [14]:
df_sub = df[df['sport']=='bike'].copy()
df_sub.reset_index(drop=1,inplace=True)
df_sub

id    userId gender sport  duration  calories   distance  \
0      396826535  10921915   male  bike      7589  1562.000  53.880000   
1      392337038  10921915   male  bike      4440   908.000  32.610000   
2      386729739  10921915   male  bike      4519   921.000  32.700000   
3      371302193  10921915   male  bike      4422   889.000  32.650000   
4      366977747  10921915   male  bike      6770  1222.000  46.370000   
...          ...       ...    ...   ...       ...       ...        ...   
25151  571917798        69   male  bike      1190   336.478   9.709200   
25152  571917904        69   male  bike      1286   373.303   9.981400   
25153  623853034        69   male  bike      5439  1198.000  43.532416   
25154  623853358        69   male  bike      5426  1129.000  43.671405   
25155  623853543        69   male  bike      5596  1196.000  43.323974   

       avg_heart_rate                                          longitude  \
0             152.650  [24.64977040886879, 24.65014273300767, 24.6509...   
1             147.710  [24.649855233728886, 24.65015547350049, 24.650...   
2             147.020  [24.649874344468117, 24.650242729112506, 24.65...   
3             145.914  [24.65018338523805, 24.650422520935535, 24.650...   
4             143.224  [24.64970293454826, 24.65009386651218, 24.6508...   
...               ...                                                ...   
25151         151.938  [166.948185, 166.94821, 166.948254, 166.948309...   
25152         155.380  [166.948344, 166.948366, 166.948437, 166.94849...   
25153         147.408  [11.97089291, 11.97083759, 11.97060299, 11.970...   
25154         140.582  [11.97151852, 11.9715023, 11.97143173, 11.9709...   
25155         144.992  [11.76475906, 11.76476288, 11.76476383, 11.764...   

                                                latitude  ...  \
0      [60.173348765820265, 60.173239801079035, 60.17...  ...   
1      [60.173247596248984, 60.17320962622762, 60.172...  ...   
2      [60.173286236822605, 60.17323946580291, 60.173...  ...   
3      [60.17324591986835, 60.17319998703897, 60.1730...  ...   
4      [60.173228066414595, 60.173104433342814, 60.17...  ...   
...                                                  ...  ...   
25151  [-11.639523, -11.639488, -11.639445, -11.63939...  ...   
25152  [-11.639403, -11.639357, -11.639261, -11.63917...  ...   
25153  [55.56586075, 55.56583786, 55.56570816, 55.565...  ...   
25154  [55.56573868, 55.56574631, 55.56576157, 55.565...  ...   
25155  [55.24071503, 55.24071503, 55.24074173, 55.240...  ...   

                                        derived_distance  \
0      [0.023920359645758085, 0.0513686868631109, 0.0...   
1      [0.01714931222251621, 0.047614484656155226, 0....   
2      [0.02104899112126496, 0.03733382239564792, 0.0...   
3      [0.014204602439679812, 0.028542833923925526, 0...   
4      [0.02565751019948074, 0.055649820287697715, 0....   
...                                                  ...   
25151  [0.004755375022161955, 0.00677446292991385, 0....   
25152  [0.005653641386970405, 0.013191290032571664, 0...   
25153  [0.004311449763158366, 0.020639913919802334, 0...   
25154  [0.0013270337976171373, 0.004752050562510226, ...   
25155  [0.0002422470355421488, 0.002977172910638461, ...   

                                           derived_speed  \
0      [10.764161840591138, 16.81157024610902, 15.919...   
1      [12.34750480021167, 14.284345396846566, 17.330...   
2      [12.629394672758975, 16.800220078041566, 20.17...   
3      [12.78414219571183, 17.125700354355313, 20.887...   
4      [10.263004079792296, 13.355956869047452, 19.92...   
...                                                  ...   
25151  [8.559675039891518, 12.19403327384493, 14.1870...   
25152  [10.17655449654673, 15.829548039085996, 20.603...   
25153  [15.521219147370116, 18.5759225278221, 15.4956...   
25154  [4.777321671421694, 2.1384227531296016, 11.015...   
25155  [0.8720893279517357, 2.679455619574615, 9.5

In [15]:
feature = ['id','distance','change_alti','diff_alti','avg_alti','min_alti','max_alti']
df_cluster = df_sub[feature]

train = df_cluster.drop('id',axis=1)
t= preprocessing.StandardScaler().fit(train)
train=t.transform(train)
train

array([[ 0.95804389,  0.87212916, -0.19680713, -0.40553436, -0.418526  ,
        -0.41297738],
       [-0.07329   , -0.07990473, -0.30097974, -0.44338141, -0.40400579,
        -0.4417235 ],
       [-0.06892611, -0.00922972, -0.289405  , -0.45942612, -0.43081233,
        -0.45879151],
       ...,
       [ 0.45631307,  0.40858427, -0.03939076, -0.44006984, -0.47213909,
        -0.39501105],
       [ 0.46305233,  0.33842894, -0.06948507, -0.37105039, -0.37161455,
        -0.32584069],
       [ 0.44620619,  0.35297967, -0.06948507, -0.38765562, -0.40400579,
        -0.35189186]])

In [16]:
%%time
ch_score = []
ss_score = []
meandistortions = []
for k in range(2,15):
    clf = KMeans(n_clusters=k)
    pred = clf.fit_predict(train)
    ch = metrics.calinski_harabasz_score(train,pred)
    ss = metrics.silhouette_score(train,pred)
    ch_score.append(ch)
    ss_score.append(ss)
    meandistortions.append(sum(np.min(cdist(train, clf.cluster_centers_, 'euclidean'), axis=1)) / train.shape[0])

Wall time: 1min 32s


In [17]:
fig = make_subplots(rows=1, cols=3,subplot_titles=("Calinski Harabasz Score", "Elbow Score",'Silhouette Score'))

fig.add_trace(go.Scatter(x=list(range(2,15)), y=ch_score,
                    mode='lines+markers',),row=1,col=1)

fig.add_trace(go.Scatter(x=list(range(2,15)), y=ss_score,
                    mode='lines+markers',
                    name='lines'),row=1,col=3,)

fig.add_trace(go.Scatter(x=list(range(2,15)), y=meandistortions,
                    mode='lines+markers',
                    name='lines'),row=1,col=2,)

fig.update_layout(height=600, width=1200, title_text="Biking: Number of K",showlegend=False)
fig.show()

In [18]:
clf = KMeans(n_clusters=5)
pred = clf.fit_predict(train)
pred = [str(i) for i in pred]

In [19]:
tsne = TSNE(n_components=2, random_state=0)
projections = tsne.fit_transform(train)

c:\Users\user\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:780: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

c:\Users\user\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:790: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



In [20]:
projections_df = pd.DataFrame(projections)
projections_df['Cluster']=pred

In [21]:
fig = px.scatter(
    projections_df, x=0, y=1,
    color='Cluster',
    labels={'color': 'Cluster'},
    category_orders={"Cluster": ["0", "1", "2", "3","4"]}
)

fig.update_layout(height=600, width=1200,title='TSNE: Biking Route Clustering',font_size=22)
fig.show()

In [22]:
t = df_cluster.copy()
t['K_means'] = pred
t = t.groupby('K_means').mean()

In [23]:
x_axis = ['Cluster '+str(i) for i in range(len(t))]
fig = go.Figure(data=[
    go.Bar(name='Distance', x=x_axis, y=t['distance']*100),
    go.Bar(name='Change of Altitude', x=x_axis, y=t['change_alti']),
    go.Bar(name='Diff_Altitude', x=x_axis, y=t['diff_alti']),
    go.Bar(name='Avg_Altitude', x=x_axis, y=t['avg_alti'])
])
# Change the bar mode
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01))
fig.update_layout(barmode='group',font_size=22,height=600,width=1200,title = 'Cluster of Biking')
fig.show()

In [24]:
df_sub['Cluster']=pred
df_bike = df_sub.copy()

Cluster for mountain bike

In [25]:
df_sub = df[df['sport']=='mountain bike'].copy()
df_sub.reset_index(drop=1,inplace=True)
df_sub

id    userId gender          sport  duration  calories  \
0     334121582  13279851   male  mountain bike      4209     585.0   
1     299896527  13279851   male  mountain bike      5205     969.0   
2     280861813  13279851   male  mountain bike      4016     695.0   
3     268331036  13279851   male  mountain bike      4593     977.0   
4     268331062  13279851   male  mountain bike      6265    1183.0   
...         ...       ...    ...            ...       ...       ...   
3438  326038483      4101   male  mountain bike      4342     979.0   
3439  325108919      4101   male  mountain bike      7991    1668.0   
3440  325107241      4101   male  mountain bike      4816    1015.0   
3441  323643540      4101   male  mountain bike      8814    1932.9   
3442  312646138   1875839   male  mountain bike      9903    3109.0   

       distance  avg_heart_rate  \
0     26.410000         123.710   
1     26.710000         149.772   
2     19.200000         141.698   
3     26.400000         138.136   
4     45.800000         137.708   
...         ...             ...   
3438  14.595000         144.944   
3439  23.995300         132.948   
3440  12.216500         134.980   
3441  24.250000         135.506   
3442  34.822441         140.098   

                                              longitude  \
0     [5.439254678785801, 5.439083268865943, 5.43904...   
1     [5.523203210905194, 5.522962063550949, 5.52271...   
2     [5.52276567555964, 5.522626284509897, 5.522374...   
3     [5.5180043, 5.5177206, 5.5170584, 5.5165136, 5...   
4     [5.5487193, 5.5486971, 5.5482386, 5.5468608, 5...   
...                                                 ...   
3438  [10.20356, 10.203871667, 10.204268333, 10.2045...   
3439  [10.204013333, 10.204566667, 10.205966667, 10....   
3440  [10.20358, 10.203926667, 10.20437, 10.204585, ...   
3441  [10.20388, 10.20465, 10.206198333, 10.20629166...   
3442  [-3.224862, -3.224578, -3.224073, -3.223615, -...   

                                               latitude  ...  \
0     [52.01802771538496, 52.017894526943564, 52.017...  ...   
1     [52.025884576141834, 52.02558291144669, 52.025...  ...   
2     [52.02590234577656, 52.02570897527039, 52.0253...  ...   
3     [52.0259099, 52.0255485, 52.0246936, 52.023993...  ...   
4     [52.0036153, 52.0037062, 52.0038875, 52.004203...  ...   
...                                                 ...  ...   
3438  [55.431498333, 55.431458333, 55.431435, 55.431...  ...   
3439  [55.431515, 55.431685, 55.43218, 55.432563333,...  ...   
3440  [55.431656667, 55.431608333, 55.431556667, 55....  ...   
3441  [55.431536667, 55.431798333, 55.432343333, 55....  ...   
3442  [54.610815, 54.611069, 54.611546, 54.612494, 5...  ...   

                                       derived_distance  \
0     [0.018902475274583067, 0.009400992108153514, 0...   
1     [0.03739824941600433, 0.04238438458152925, 0.0...   
2     [0.02355992050528061, 0.03855914048723234, 0.0...   
3     [0.044642134006436636, 0.10533897946360782, 0....   
4     [0.010232248372871601, 0.03731884619806046, 0....   
...                                                 ...   
3438  [0.020166490148327013, 0.025168122109977153, 0...   
3439  [0.03972465658606036, 0.10412458317327904, 0.0...   
3440  [0.0225514122381834, 0.028633074860945698, 0.0...   
3441  [0.05665325215438958, 0.1149959416241168, 0.03...   
3442  [0.03381280497543025, 0.06229696198002355, 0.1...   

                                          derived_speed  \
0     [11.34148516474984, 11.281190529784217, 12.608...   
1     [11.219474824801297, 15.25837844935053, 17.691...   
2     [12.116530545572886, 17.351613219254556, 17.69...   
3     [20.088960302896485, 22.307078004058127, 22.21...   
4     [9.209023535584441, 19.19254947328824, 21.3223...   
...                                                 ...   
3438  [9.074920566747156, 10.06724884399086, 13.9825...   
3439  [9.533917580654485, 23.428031213987783, 10.850...   
3440  [9.020564895273

In [26]:
feature = ['id','distance','change_alti','diff_alti','avg_alti','min_alti','max_alti']
df_cluster = df_sub[feature]

train = df_cluster.drop('id',axis=1)
t= preprocessing.StandardScaler().fit(train)
train=t.transform(train)
train

array([[ 0.004527  , -0.75684474, -0.62913834, -0.55552803, -0.47894004,
        -0.57925992],
       [ 0.02397418,  0.07863727, -0.40621659, -0.4956471 , -0.46043416,
        -0.50557628],
       [-0.46285375, -0.34658566, -0.41566242, -0.50494518, -0.46548122,
        -0.51240788],
       ...,
       [-0.91555186, -0.38607362, -0.60646833, -0.4814069 , -0.43744201,
        -0.5372944 ],
       [-0.13549275,  0.54085418, -0.55923915, -0.46537245, -0.4094028 ,
        -0.50069657],
       [ 0.54985475,  3.68229769,  1.63103323,  0.29598729,  0.11681183,
         0.52293999]])

In [27]:
%%time
ch_score = []
ss_score = []
meandistortions = []
for k in range(2,15):
    clf = KMeans(n_clusters=k)
    pred = clf.fit_predict(train)
    ch = metrics.calinski_harabasz_score(train,pred)
    ss = metrics.silhouette_score(train,pred)
    ch_score.append(ch)
    ss_score.append(ss)
    meandistortions.append(sum(np.min(cdist(train, clf.cluster_centers_, 'euclidean'), axis=1)) / train.shape[0])

Wall time: 3.78 s


In [28]:
fig = make_subplots(rows=1, cols=3,subplot_titles=("Calinski Harabasz Score", "Elbow Score",'Silhouette Score'))

fig.add_trace(go.Scatter(x=list(range(2,15)), y=ch_score,
                    mode='lines+markers',),row=1,col=1)

fig.add_trace(go.Scatter(x=list(range(2,15)), y=ss_score,
                    mode='lines+markers',
                    name='lines'),row=1,col=3,)

fig.add_trace(go.Scatter(x=list(range(2,15)), y=meandistortions,
                    mode='lines+markers',
                    name='lines'),row=1,col=2,)

fig.update_layout(height=600, width=1200, title_text="Mountain Bike: Number of K",showlegend=False)
fig.show()

In [29]:
clf = KMeans(n_clusters=3)
pred = clf.fit_predict(train)
pred = [str(i) for i in pred]

In [30]:
tsne = TSNE(n_components=2, random_state=0)
projections = tsne.fit_transform(train)

c:\Users\user\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:780: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

c:\Users\user\anaconda3\lib\site-packages\sklearn\manifold\_t_sne.py:790: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



In [31]:
projections_df = pd.DataFrame(projections)
projections_df['Cluster']=pred

In [32]:
fig = px.scatter(
    projections_df, x=0, y=1,
    color='Cluster',
    labels={'color': 'Cluster'},
    category_orders={"Cluster": ["0", "1", "2", "3","4"]}
)

fig.update_layout(height=600, width=1200,title='TSNE: Mountain Biking Route Clustering',font_size=22)
fig.show()

In [33]:
t = df_cluster.copy()
t['K_means'] = pred
t = t.groupby('K_means').mean()

In [34]:
x_axis = ['Cluster '+str(i) for i in range(len(t))]
fig = go.Figure(data=[
    go.Bar(name='Distance', x=x_axis, y=t['distance']*100),
    go.Bar(name='Change of Altitude', x=x_axis, y=t['change_alti']),
    go.Bar(name='Diff_Altitude', x=x_axis, y=t['diff_alti']),
    go.Bar(name='Avg_Altitude', x=x_axis, y=t['avg_alti'])
])
# Change the bar mode
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01))
fig.update_layout(barmode='group',font_size=22,height=600,width=1200,title = 'Cluster of Mountain Biking')
fig.show()

In [35]:
df_sub['Cluster']=pred
df_mountain = df_sub.copy()

Merge

In [36]:
df_all = df_run.copy()
df_all = df_all.append(df_bike)
df_all = df_all.append(df_mountain)
df_all.reset_index(drop=1,inplace=True)
df_all

C:\Users\user\AppData\Local\Temp\ipykernel_4756\105301971.py:2: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\user\AppData\Local\Temp\ipykernel_4756\105301971.py:3: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



id   userId gender          sport  duration  calories  \
0      321063199  4969375   male            run      3888     436.0   
1      303565793  4969375   male            run      4204     577.0   
2      296982347  4969375   male            run      6503    1025.0   
3      295890426  4969375   male            run      5118     775.0   
4      294163731  4969375   male            run      3035     445.0   
...          ...      ...    ...            ...       ...       ...   
65495  326038483     4101   male  mountain bike      4342     979.0   
65496  325108919     4101   male  mountain bike      7991    1668.0   
65497  325107241     4101   male  mountain bike      4816    1015.0   
65498  323643540     4101   male  mountain bike      8814    1932.9   
65499  312646138  1875839   male  mountain bike      9903    3109.0   

        distance  avg_heart_rate  \
0       8.650000         122.104   
1      14.370000         146.994   
2      22.220000         134.918   
3      16.980000         132.414   
4       9.670000         125.346   
...          ...             ...   
65495  14.595000         144.944   
65496  23.995300         132.948   
65497  12.216500         134.980   
65498  24.250000         135.506   
65499  34.822441         140.098   

                                               longitude  \
0      [6.8854929, 6.8853678, 6.8851621, 6.8848205, 6...   
1      [6.9144073, 6.9142929, 6.9141539, 6.9140268, 6...   
2      [6.8678543, 6.8678634, 6.8675429, 6.8672183, 6...   
3      [6.9143328, 6.9146396, 6.9148949, 6.9151568, 6...   
4      [6.9133737, 6.9132722, 6.913217, 6.9131066, 6....   
...                                                  ...   
65495  [10.20356, 10.203871667, 10.204268333, 10.2045...   
65496  [10.204013333, 10.204566667, 10.205966667, 10....   
65497  [10.20358, 10.203926667, 10.20437, 10.204585, ...   
65498  [10.20388, 10.20465, 10.206198333, 10.20629166...   
65499  [-3.224862, -3.224578, -3.224073, -3.223615, -...   

                                                latitude  ...  \
0      [52.2226809, 52.222727, 52.2228258, 52.2228606...  ...   
1      [52.2111711, 52.2112631, 52.2114064, 52.211608...  ...   
2      [52.1936673, 52.1934354, 52.1931993, 52.192873...  ...   
3      [52.2112195, 52.2110264, 52.2108135, 52.210601...  ...   
4      [52.2111481, 52.2111209, 52.21119, 52.2112981,...  ...   
...                                                  ...  ...   
65495  [55.431498333, 55.431458333, 55.431435, 55.431...  ...   
65496  [55.431515, 55.431685, 55.43218, 55.432563333,...  ...   
65497  [55.431656667, 55.431608333, 55.431556667, 55....  ...   
65498  [55.431536667, 55.431798333, 55.432343333, 55....  ...   
65499  [54.610815, 54.611069, 54.611546, 54.612494, 5...  ...   

                                           derived_speed  \
0      [12.698946852577029, 10.911666227748753, 10.05...   
1      [5.790011898354694, 7.923126352508781, 8.85172...   
2      [7.1452896790820954, 9.460093775795364, 10.251...   
3      [10.820442933212894, 10.685701145251175, 10.36...   
4      [5.368254738393704, 6.557825426283524, 7.28499...   
...                                                  ...   
65495  [9.074920566747156, 10.06724884399086, 13.9825...   
65496  [9.533917580654485, 23.428031213987783, 10.850...   
65497  [9.02056489527336, 10.30790694994045, 8.784995...   
65498  [11.997159279753086, 22.99918832482336, 6.5228...   
65499  [17.3894425587927, 18.689088594007064, 16.4463...   

                                            time_elapsed validate    avg_alti  \
0      [7, 8, 8, 8, 7, 8, 8, 8, 8, 7, 8, 8, 8, 8, 7, ...     True  -31.706000   
1      [8, 8, 9, 8, 9, 8, 9, 8, 8, 9, 8, 9, 8, 9, 8, ...     True   41.671200   
2      [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 1...     True   34.125600   
3      [10, 10, 10, 11, 10, 10, 10, 11, 10, 10, 10, 1...     True   45.097200   
4      [6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 7, 6, 6, 6, ...     True   48.845600   
...                

In [37]:
df_all.to_csv('D:\MiniProject_P3_fitrec\endomondo_RouteCluster.csv',index=0)